In [1]:
# --- Setup & Imports ---
import os, sys
from pathlib import Path
import pandas as pd
import numpy as np

# --- 1. Pfad-Setup ---
def _locate_repo_root(start: Path) -> Path:
    cur = start.resolve()
    for _ in range(5):  # walk up to 5 levels
        if (cur / 'src').exists():
            return cur
        if cur.parent == cur:
            break
        cur = cur.parent
    return start.resolve()

NOTEBOOK_DIR = Path.cwd()
PROJECT_ROOT = _locate_repo_root(NOTEBOOK_DIR)
os.environ['PROJECT_ROOT'] = str(PROJECT_ROOT)
if str(PROJECT_ROOT) not in sys.path:
    sys.path.insert(0, str(PROJECT_ROOT))

from src.config import GlobalConfig, DEFAULT_CORR_SPEC, outputs_for_model
from src.tuning import run_stageA, run_stageB
from src.io_timesplits import load_target, load_ifo_features
# --- MODELL-IMPORT ---
from src.models.LGBM import ForecastModel # Nutzt LightGBM

print('PROJECT_ROOT =', PROJECT_ROOT)

# --- MODELLNAME ---
MODEL_NAME = "lightgbm"
outputs_for_model(MODEL_NAME)
print(f'Modell {MODEL_NAME} wird getunt.')

# --- 2. Daten laden ---
y = load_target()  # ΔIP with DatetimeIndex
X_ifo = load_ifo_features() # ifo features

idx = y.index.intersection(X_ifo.index)
y, X_ifo = y.loc[idx], X_ifo.loc[idx]
print('Shapes:', X_ifo.shape, y.shape)

# --- 3. Base config (splits & policy as in thesis) ---
def base_cfg() -> GlobalConfig:
    cfg = GlobalConfig()
    cfg.W0_A     = 180
    cfg.BLOCKS_A = [(181,200), (201,220), (221,240)]
    cfg.W0_B     = 240
    # Policy Parameter
    cfg.policy_window   = 24
    cfg.policy_decay    = 0.95
    cfg.policy_gain_min = 0.03
    cfg.policy_cooldown = 3
    return cfg

cfg0 = base_cfg()

# --- 4. Helper für Korrelations-Spezifikation ---
def make_corr_spec(kind: str) -> dict:
    spec = dict(DEFAULT_CORR_SPEC)
    spec['mode'] = kind
    return spec

# Nur eine Corr-Option für Minimalismus
corr_options = [
    ("expanding", make_corr_spec("expanding")),
]

# --- 5. MINIMALISTISCHES TUNING-GRID (Einzelne Parameter) ---

# A) Feature Engineering Parameter
lag_candidates_list = [(1, 2, 3, 6, 12)]
top_k_lags_list = [1]
use_rm3_list = [True]
k1_topk_list = [100, 200] # Screening
redundancy_param_list = [0.90]
dr_options_list = [
    {'dr_method': 'none'},
    {'dr_method': 'pca', 'pca_var_target': 0.95, 'pca_kmax': 50}
]

# B) LightGBM Hyperparameter
learning_rate_list = [0.1, 0.05]
num_leaves_list = [7, 15]
max_depth_list = [3, 4]
min_child_samples_list = [20, 30]
n_estimators_list = [1000] # Fest für Early Stopping
early_stopping_rounds_list = [50] # Fest für Early Stopping

# C) Target Blocks & Weighting
target_block_options = [ None, ["AR1"] ]
weighting_options = [ {"sample_weight_decay": None} ]

# D) Grid zusammensetzen
def build_model_grid():
    hp_grid = []
    for corr_tag, corr_spec in corr_options:
        for lags in lag_candidates_list:
            for k_lags in top_k_lags_list:
                for rm3 in use_rm3_list:
                    for k1 in k1_topk_list:
                        for red in redundancy_param_list:
                            for dr_opt in dr_options_list:
                                # Logik, um ungültige FE/DR-Kombinationen zu vermeiden
                                if k1 == 100 and dr_opt['dr_method'] != 'none': continue
                                if k1 == 200 and dr_opt['dr_method'] == 'none': continue

                                for lr in learning_rate_list:
                                    for leaves in num_leaves_list:
                                        for depth in max_depth_list:
                                            # Logik für gültige Leaves/Depth Kombi (optional, aber gut)
                                            if leaves > 2**depth: continue

                                            for min_child in min_child_samples_list:
                                                for n_est in n_estimators_list:
                                                    for esr in early_stopping_rounds_list:
                                                        for block_set in target_block_options:
                                                            for weight_hp in weighting_options:
                                                                hp = {
                                                                    # FE Params
                                                                    'lag_candidates': lags,
                                                                    'top_k_lags_per_feature': k_lags,
                                                                    'use_rm3': rm3,
                                                                    'k1_topk': k1,
                                                                    'redundancy_param': red,
                                                                    **dr_opt,
                                                                    # LGBM Params
                                                                    'learning_rate': lr,
                                                                    'num_leaves': leaves,
                                                                    'max_depth': depth,
                                                                    'min_child_samples': min_child,
                                                                    'n_estimators': n_est,
                                                                    'early_stopping_rounds': esr,
                                                                    # Other Params
                                                                    **weight_hp,
                                                                    'corr_tag': corr_tag,
                                                                    'corr_spec': corr_spec,
                                                                    'target_block_set': block_set
                                                                }
                                                                hp_grid.append(hp)
    return hp_grid

model_grid = build_model_grid()
print("HP-Kombinationen:", len(model_grid))
# Erwartet: 1(Corr)*1*1*1 * (1*1 + 1*1)(FE/DR) * 1*1 * 2(LR)*2(Leaves)*2(Depth)*2(Child)*1(N_est)*1(ESR)*2(Blocks)*1(Weight) = 2 * 32 = 64
# Aber durch `if leaves > 2**depth: continue` und `if k1/dr logic` reduziert sich das.
print("Erstes HP-Set:", model_grid[0] if model_grid else "Grid ist leer")


# --- 6. Stage A/B Lauf ---
if model_grid:
    shortlist = run_stageA(
        model_name=MODEL_NAME,
        model_ctor=lambda hp: ForecastModel(hp),
        model_grid=model_grid,
        X=X_ifo, y=y, cfg=cfg0,
        keep_top_k_final=min(5, len(model_grid)),
        min_survivors_per_block=max(1, len(model_grid)//2),
    )

    run_stageB(
        model_name=MODEL_NAME,
        model_ctor=lambda hp: ForecastModel(hp),
        shortlist=shortlist,
        X=X_ifo, y=y, cfg=cfg0,
        # max_months=12,   # Optional: Begrenze Stage B für schnellen Test
    )
else:
    print("Keine gültigen HP-Kombinationen gefunden, Stages übersprungen.")


print(f"\nDone. Check outputs/stageA|stageB/{MODEL_NAME} for results.")

PROJECT_ROOT = /Users/jonasschernich/Documents/Masterarbeit/Code
Modell lightgbm wird getunt.
INFO in load_ifo_features: Renaming columns to ensure validity.
Shapes: (407, 2160) (407,)
HP-Kombinationen: 8
Erstes HP-Set: {'lag_candidates': (1, 2, 3, 6, 12), 'top_k_lags_per_feature': 1, 'use_rm3': True, 'k1_topk': 100, 'redundancy_param': 0.9, 'dr_method': 'none', 'learning_rate': 0.1, 'num_leaves': 7, 'max_depth': 3, 'min_child_samples': 20, 'n_estimators': 1000, 'early_stopping_rounds': 50, 'sample_weight_decay': None, 'corr_tag': 'expanding', 'corr_spec': {'mode': 'expanding', 'window': None, 'lam': None}, 'target_block_set': None}
[Stage A][Block 1] train_end=180, OOS=181-200 | configs=8
  - Config 1/8
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.001049 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 3769
[LightGBM] [Info] Number of data points in the train set: 144, number of used features: 76